<a href="https://colab.research.google.com/github/KarolMc/msc_dissertation/blob/main/feature_selection.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import joblib

import pandas as pd
import numpy as np

# Import SVC from sklearn.svm and accuracy_score from sklearn.metrics
from sklearn.svm import SVC
from sklearn.metrics import accuracy_score

import matplotlib.pyplot as plt

import seaborn as sns

from sklearn.model_selection import train_test_split, StratifiedKFold

from sklearn.preprocessing import StandardScaler
import xgboost as xgb
from sklearn.ensemble import RandomForestClassifier

from sklearn.pipeline import Pipeline

from sklearn.model_selection import GridSearchCV


from sklearn.model_selection import RandomizedSearchCV

from sklearn.metrics import make_scorer

import random

random_seed = random.seed(42)

from sklearn.preprocessing import LabelEncoder

from sklearn.metrics import accuracy_score, confusion_matrix

from sklearn.metrics import confusion_matrix, ConfusionMatrixDisplay, classification_report
import matplotlib.pyplot as plt

# PCA on Reduced Data

In [ ]:
X_train = pd.read_csv('Data/X_train_reduced.csv', index_col=[0])
y_train = pd.read_csv('Data/y_train_SMOV.csv', index_col=[0])
X_test = pd.read_csv('Data/X_test_reduced.csv', index_col=[0])
y_test = pd.read_csv('Data/y_test.csv', index_col=[0])

train_features = X_train.columns

In [ ]:
diabetes_data = X_train

In [ ]:
diabetes_data.head()

SEQN  Age_Years  Household_size  Family_income_poverty_ratio  \
0  71180       57.0             7.0                         1.80   
1  66825        8.0             4.0                         1.56   
2  83409       43.0             7.0                         0.54   
3  83957        0.0             4.0                         0.49   
4  70223       47.0             7.0                         0.79   

   Folic_acid_nmol_l  Albumin_urine_ug_ml  Creatinine_unrine_umol_l  \
0               0.68                  5.6                    7248.8   
1               0.68                 13.6                   10342.8   
2               0.68                 24.2                    6541.6   
3               0.68                  8.4                    7072.0   
4               0.68                113.0                   33503.6   

   White_Blood_Cell_Count  Basophils_percent  Lymphocyte_number  ...  \
0                     8.4       5.397605e-79                2.1  ...   
1                     6.1       2.200000e+00                2.1  ...   
2                     8.6       8.000000e-01                3.6  ...   
3                     6.9       6.000000e-01                2.2  ...   
4                     6.3       6.000000e-01                2.0  ...   

   Decayed_teeth  Gum_disease  BPCuff_Child  BPCuff_Large  BPCuff_Thigh  \
0              0            0             0             0             0   
1              0            0             1             0             0   
2              1            1             0             1             0   
3              0            0             0             0             0   
4              0            1             0             1             0   

   Pulse_irregular  BMI_Obese  BMI_Overweight  BMI_Underweight  BMI_unknown  
0                0          0               0                0            0  
1                0          0               0                1            0  
2                0          1               0                0            0  
3                0          0               0                0            1  
4                1          1               0                0            0  

[5 rows x 156 columns]

In [ ]:
diabetes_labels = y_train

diabetes_labels = diabetes_labels.rename({'0': 'Diabetes_status'}, axis = 1)
diabetes_labels.head()

Diabetes_status
0                0
1                0
2                1
3                0
4                0

In [ ]:
diabetes_training_reduced_data = pd.concat([diabetes_data, diabetes_labels], axis = 1)
diabetes_training_reduced_data = diabetes_training_reduced_data.drop('SEQN', axis = 1)
diabetes_training_reduced_data.shape

(75864, 156)

In [ ]:
diabetes_training_reduced_data.head()

Age_Years  Household_size  Family_income_poverty_ratio  Folic_acid_nmol_l  \
0       57.0             7.0                         1.80               0.68   
1        8.0             4.0                         1.56               0.68   
2       43.0             7.0                         0.54               0.68   
3        0.0             4.0                         0.49               0.68   
4       47.0             7.0                         0.79               0.68   

   Albumin_urine_ug_ml  Creatinine_unrine_umol_l  White_Blood_Cell_Count  \
0                  5.6                    7248.8                     8.4   
1                 13.6                   10342.8                     6.1   
2                 24.2                    6541.6                     8.6   
3                  8.4                    7072.0                     6.9   
4                113.0                   33503.6                     6.3   

   Basophils_percent  Lymphocyte_number  Monocyte_number  ...  Gum_disease  \
0       5.397605e-79                2.1              0.8  ...            0   
1       2.200000e+00                2.1              0.1  ...            0   
2       8.000000e-01                3.6              0.5  ...            1   
3       6.000000e-01                2.2              0.5  ...            0   
4       6.000000e-01                2.0              0.7  ...            1   

   BPCuff_Child  BPCuff_Large  BPCuff_Thigh  Pulse_irregular  BMI_Obese  \
0             0             0             0                0          0   
1             1             0             0                0          0   
2             0             1             0                0          1   
3             0             0             0                0          0   
4             0             1             0                1          1   

   BMI_Overweight  BMI_Underweight  BMI_unknown  Diabetes_status  
0               0                0            0                0  
1               0                1            0                0  
2               0                0            0                1  
3               0                0            1                0  
4               0                0            0                0  

[5 rows x 156 columns]

In [ ]:
diabetes_training_reduced_data['Diabetes_status'].value_counts()

0    25288
1    25288
2    25288
Name: Diabetes_status, dtype: int64

In [ ]:
features = list(diabetes_training_reduced_data.columns)

In [ ]:
# correlations

In [ ]:
# import libraries
import matplotlib.pyplot as plt
import seaborn as sns

# set figure size
plt.figure(figsize=(180, 180))

# Generate a mask to onlyshow the bottom triangle
mask = np.triu(np.ones_like(diabetes_training_reduced_data.corr(), dtype=bool))

# generate heatmap
sns_plt = sns.heatmap(diabetes_training_reduced_data.corr(), annot=True, mask=mask, vmin=-1, vmax=1, cmap = 'coolwarm')
plt.title('Correlation Coefficient Of Predictors')
plt.show()

## Feature Selection

In [ ]:
!pip install statsmodels

In [ ]:
# load statmodels functions
from statsmodels.stats.outliers_influence import variance_inflation_factor
from statsmodels.tools.tools import add_constant

# compute the vif for all given features
def compute_vif(considered_features):
    
    X = diabetes_training_reduced_data[considered_features]
    # the calculation of variance inflation requires a constant
    X['intercept'] = 1
    
    # create dataframe to store vif values
    vif = pd.DataFrame()
    vif["Variable"] = X.columns
    vif["VIF"] = [variance_inflation_factor(X.values, i) for i in range(X.shape[1])]
    vif = vif[vif['Variable']!='intercept']
    return vif

In [ ]:
vifs_df = compute_vif(features)

In [ ]:
vif_df = vifs_df.sort_values(by=['VIF'], ascending = False)
vif_df
# vif_df = vif_df.replace([np.inf, -np.inf], np.nan, inplace=True)
# vif_df.head()
# vif_df = vif_df.dropna(subset=["VIF"], how="all", inplace=True)
# vif_df = vif_df[vif_df.VIF < inf]
# vif_df.head(30)

Variable          VIF
22          Urinary_perchlorate_ng_ml  1772.124439
23              Urinary_nitrate_ng_ml  1772.052113
15                Haematocrit_percent   489.178774
14                   Haemoglobin_g_dl   374.319013
71                  Total_Protein_g_L   259.055990
..                                ...          ...
150                   Pulse_irregular     1.032301
139                chlamydia_positive     1.027919
144                     HEPD_positive     1.022923
84   5_Formyl_tetrahydrofolate_nmol_L     1.010983
34                Urinary_Iodine_ug_l     1.005050

[156 rows x 2 columns]

In [ ]:
high_vif_df = vif_df[vif_df['VIF']<5000]

In [ ]:
high_vif_df = high_vif_df[high_vif_df['VIF']>5]


In [ ]:
high_vif_df

Variable          VIF
22                  Urinary_perchlorate_ng_ml  1772.124439
23                      Urinary_nitrate_ng_ml  1772.052113
15                        Haematocrit_percent   489.178774
14                           Haemoglobin_g_dl   374.319013
71                          Total_Protein_g_L   259.055990
78                               Globulin_g_L   249.316687
6                      White_Blood_Cell_Count   240.393623
16                        Mean_Cell_Volume_fl   229.766814
17                   Mean_Cell_Haemoglobin_pg   210.267416
58                                Albumin_g_l   139.357593
10               Segmented_neutrophils_number   136.076103
13                             Red_Cell_count   105.362513
8                           Lymphocyte_number    66.393917
18   Mean_Cell_Haemoglobin_Concentration_g_dl    57.151017
90                                  Weight_kg    36.415744
92                      Body_Mass_Index_kg_m2    23.443090
26                 Urinary_arsenous_acid_ug_l    18.030982
95                       Arm_circumference_cm    11.869723
27                  Urinary_Arsenic_Acid_ug_l    11.285880
94                        Upper_Arm_Length_cm    10.129091
96                     Waist_Circumference_cm     9.900949
91                         Height_Standing_cm     9.253014
0                                   Age_Years     7.626359
74                              Sodium_mmol_L     6.115432
77                         Osmolality_mmol_Kg     5.470525
154                               BMI_unknown     5.353070

In [ ]:
high_vif_variables = high_vif_df['Variable'].to_list()

high_vif_variables

['Urinary_perchlorate_ng_ml',
 'Urinary_nitrate_ng_ml',
 'Haematocrit_percent',
 'Haemoglobin_g_dl',
 'Total_Protein_g_L',
 'Globulin_g_L',
 'White_Blood_Cell_Count',
 'Mean_Cell_Volume_fl',
 'Mean_Cell_Haemoglobin_pg',
 'Albumin_g_l',
 'Segmented_neutrophils_number',
 'Red_Cell_count',
 'Lymphocyte_number',
 'Mean_Cell_Haemoglobin_Concentration_g_dl',
 'Weight_kg',
 'Body_Mass_Index_kg_m2',
 'Urinary_arsenous_acid_ug_l',
 'Arm_circumference_cm',
 'Urinary_Arsenic_Acid_ug_l',
 'Upper_Arm_Length_cm',
 'Waist_Circumference_cm',
 'Height_Standing_cm',
 'Age_Years',
 'Sodium_mmol_L',
 'Osmolality_mmol_Kg',
 'BMI_unknown']

In [ ]:
# CORRELATIONS

In [ ]:
reduced_columns = list(diabetes_training_reduced_data.columns)

reduced_columns.pop()

reduced_columns

['Age_Years',
 'Household_size',
 'Family_income_poverty_ratio',
 'Folic_acid_nmol_l',
 'Albumin_urine_ug_ml',
 'Creatinine_unrine_umol_l',
 'White_Blood_Cell_Count',
 'Basophils_percent',
 'Lymphocyte_number',
 'Monocyte_number',
 'Segmented_neutrophils_number',
 'Eosinophils_number',
 'Basophils_number',
 'Red_Cell_count',
 'Haemoglobin_g_dl',
 'Haematocrit_percent',
 'Mean_Cell_Volume_fl',
 'Mean_Cell_Haemoglobin_pg',
 'Mean_Cell_Haemoglobin_Concentration_g_dl',
 'Red_Cell_Distribution_Width_Percent',
 'Platelet_Count',
 'Mean_Platelet_Volumne_fl',
 'Urinary_perchlorate_ng_ml',
 'Urinary_nitrate_ng_ml',
 'Urinary_Thiocyanate_ng_ml',
 'Urinary_Total_Arsenic_ug_l',
 'Urinary_arsenous_acid_ug_l',
 'Urinary_Arsenic_Acid_ug_l',
 'Urinary_Arsenobetaine_ug_l',
 'Urinary_Arsenocholine_ug_l',
 'Urinary_DimethylArsinic_Acid_ug_l',
 'Urinary_Monomethylarsonic_acid_ug_l',
 'Urinary_Trimethylarsine_Oxide_ug_l',
 'Klotho_pg_ml',
 'Urinary_Iodine_ug_l',
 'Cotinine_ng_ml',
 'Total_Cholesterol_mmol_

In [ ]:
X_train_reduced = X_train[reduced_columns]

X_train_reduced.shape

(75864, 155)

In [ ]:
X_test_reduced = X_test[reduced_columns]

X_test_reduced.shape

(12178, 155)

In [ ]:
# Feature selection

In [ ]:
from sklearn.feature_selection import chi2, f_classif, mutual_info_classif

In [ ]:
from sklearn.feature_selection import SelectKBest, SequentialFeatureSelector, RFE

In [ ]:
!pip install lightgbm

In [ ]:
import lightgbm

In [ ]:
lgbm = lightgbm.LGBMClassifier()

# Feature Selection with RFE

In [ ]:
estimator = lgbm
selectior = RFE(lgbm, n_features_to_select = 0.3, step = 1)

In [ ]:
le = LabelEncoder()
y_train = le.fit_transform(y_train)

y_test = le.fit_transform(y_test)

X_train_val, X_validation, y_train_val, y_validation = train_test_split(X_train_reduced, y_train, test_size=0.25)

/usr/local/lib/python3.9/dist-packages/sklearn/preprocessing/_label.py:115: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


In [ ]:
training_data = {'X_train':X_train_val,'y_train':y_train_val,
                'X_val': X_validation,'y_val':y_validation,
                'X_test': X_test_reduced,'y_test':y_test}

In [ ]:
selector = selectior.fit(training_data['X_train'].values, training_data['y_train'], 
          eval_set=[(training_data['X_train'].values, training_data['y_train']), (training_data['X_val'].values, training_data['y_val'])],
          verbose=10)

/usr/local/lib/python3.9/dist-packages/lightgbm/sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[10]	valid_0's multi_logloss: 0.640239	valid_1's multi_logloss: 0.652289
[20]	valid_0's multi_logloss: 0.502494	valid_1's multi_logloss: 0.522562
[30]	valid_0's multi_logloss: 0.433416	valid_1's multi_logloss: 0.460806
[40]	valid_0's multi_logloss: 0.389213	valid_1's multi_logloss: 0.423552
[50]	valid_0's multi_logloss: 0.357155	valid_1's multi_logloss: 0.397644
[60]	valid_0's multi_logloss: 0.332216	valid_1's multi_logloss: 0.379314
[70]	valid_0's multi_logloss: 0.311343	valid_1's multi_logloss: 0.364797
[80]	valid_0's multi_logloss: 0.293842	valid_1's multi_logloss: 0.35339
[90]	valid_0's multi_logloss: 0.278576	valid_1's multi_logloss: 0.343628
[100]	valid_0's multi_logloss: 0.264714	valid_1's multi_logloss: 0.335518


/usr/local/lib/python3.9/dist-packages/lightgbm/sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[10]	valid_0's multi_logloss: 0.641387	valid_1's multi_logloss: 0.653265
[20]	valid_0's multi_logloss: 0.513251	valid_1's multi_logloss: 0.53193
[30]	valid_0's multi_logloss: 0.442399	valid_1's multi_logloss: 0.468435
[40]	valid_0's multi_logloss: 0.396939	valid_1's multi_logloss: 0.429976
[50]	valid_0's multi_logloss: 0.363983	valid_1's multi_logloss: 0.403261
[60]	valid_0's multi_logloss: 0.338432	valid_1's multi_logloss: 0.384334
[70]	valid_0's multi_logloss: 0.317025	valid_1's multi_logloss: 0.369305
[80]	valid_0's multi_logloss: 0.299132	valid_1's multi_logloss: 0.357568
[90]	valid_0's multi_logloss: 0.28361	valid_1's multi_logloss: 0.347514
[100]	valid_0's multi_logloss: 0.269559	valid_1's multi_logloss: 0.339273


/usr/local/lib/python3.9/dist-packages/lightgbm/sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


...

[10]	valid_0's multi_logloss: 0.915258	valid_1's multi_logloss: 0.916226
[20]	valid_0's multi_logloss: 0.913145	valid_1's multi_logloss: 0.914982
[30]	valid_0's multi_logloss: 0.991003	valid_1's multi_logloss: 0.99328
[40]	valid_0's multi_logloss: 1.0501	valid_1's multi_logloss: 1.05352
[50]	valid_0's multi_logloss: 1.09489	valid_1's multi_logloss: 1.09945
[60]	valid_0's multi_logloss: 1.19821	valid_1's multi_logloss: 1.20275
[70]	valid_0's multi_logloss: 1.1616	valid_1's multi_logloss: 1.16568
[80]	valid_0's multi_logloss: 1.21239	valid_1's multi_logloss: 1.21546
[90]	valid_0's multi_logloss: 1.20272	valid_1's multi_logloss: 1.20577
[100]	valid_0's multi_logloss: 1.25747	valid_1's multi_logloss: 1.25966


/usr/local/lib/python3.9/dist-packages/lightgbm/sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[10]	valid_0's multi_logloss: 1.06484	valid_1's multi_logloss: 1.06664
[20]	valid_0's multi_logloss: 1.17977	valid_1's multi_logloss: 1.18092
[30]	valid_0's multi_logloss: 1.19012	valid_1's multi_logloss: 1.19061
[40]	valid_0's multi_logloss: 1.32616	valid_1's multi_logloss: 1.32548
[50]	valid_0's multi_logloss: 1.52181	valid_1's multi_logloss: 1.52093
[60]	valid_0's multi_logloss: 1.64311	valid_1's multi_logloss: 1.64061
[70]	valid_0's multi_logloss: 1.83741	valid_1's multi_logloss: 1.83386
[80]	valid_0's multi_logloss: 2.1869	valid_1's multi_logloss: 2.17974
[90]	valid_0's multi_logloss: 2.3841	valid_1's multi_logloss: 2.37513
[100]	valid_0's multi_logloss: 2.44766	valid_1's multi_logloss: 2.4391


/usr/local/lib/python3.9/dist-packages/lightgbm/sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[10]	valid_0's multi_logloss: 0.92578	valid_1's multi_logloss: 0.926434
[20]	valid_0's multi_logloss: 0.934192	valid_1's multi_logloss: 0.937409
[30]	valid_0's multi_logloss: 1.01213	valid_1's multi_logloss: 1.01654
[40]	valid_0's multi_logloss: 1.05355	valid_1's multi_logloss: 1.05838
[50]	valid_0's multi_logloss: 1.13938	valid_1's multi_logloss: 1.14398
[60]	valid_0's multi_logloss: 1.20061	valid_1's multi_logloss: 1.20535
[70]	valid_0's multi_logloss: 1.28407	valid_1's multi_logloss: 1.28891
[80]	valid_0's multi_logloss: 1.3502	valid_1's multi_logloss: 1.35568
[90]	valid_0's multi_logloss: 1.3916	valid_1's multi_logloss: 1.39806
[100]	valid_0's multi_logloss: 1.50854	valid_1's multi_logloss: 1.51627


In [ ]:
lgbm_mask = selector.support_

In [ ]:
reduced_X = X_train_reduced.loc[:, lgbm_mask]

len(reduced_X.columns)

46

In [ ]:
RFE_features = list(reduced_X.columns)

In [ ]:
RFE_features

['Age_Years',
 'Family_income_poverty_ratio',
 'Albumin_urine_ug_ml',
 'Creatinine_unrine_umol_l',
 'White_Blood_Cell_Count',
 'Lymphocyte_number',
 'Monocyte_number',
 'Eosinophils_number',
 'Basophils_number',
 'Haemoglobin_g_dl',
 'Mean_Cell_Haemoglobin_pg',
 'Mean_Cell_Haemoglobin_Concentration_g_dl',
 'Red_Cell_Distribution_Width_Percent',
 'Mean_Platelet_Volumne_fl',
 'Urinary_Thiocyanate_ng_ml',
 'Klotho_pg_ml',
 'Cotinine_ng_ml',
 'Total_Cholesterol_mmol_l',
 'Direct_HDL_Cholesterol_mmol_l',
 '25_hydroxyvitamin_D2+D3',
 'Blood_Cadmium_umol_l',
 'Blood_lead_umol_l',
 'Total_Blood_Mercury_umol_l',
 'Triglyceride_mmol_l',
 'LDL_Cholesterol_mmol_l',
 'Albumin_g_l',
 'Asparate_aminotransferase_AST_U_L',
 'Alkaline_phosphotase_U_L',
 'Blood_urea_nitrogen_mmol_L',
 'Creatinine_umol_L',
 'Gamma_Glutamyl_Transferase_U_l',
 'Total_Bilirubin_umol_L',
 'Triglycerides_refrig_serum_mmol_L',
 'Uric_acid_umol_L',
 'Sodium_mmol_L',
 'Potassium_mmol_L',
 'Chloride_mmol_L',
 'Osmolality_mmol_Kg',

# Feature Selection with Select K Best

In [ ]:
clf = lgbm
clf = clf.fit(training_data['X_train'].values, training_data['y_train'], 
          eval_set=[(training_data['X_train'].values, training_data['y_train']), (training_data['X_val'].values, training_data['y_val'])],
          verbose=10)
clf.feature_importances_  


/usr/local/lib/python3.9/dist-packages/lightgbm/sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[10]	valid_0's multi_logloss: 0.640239	valid_1's multi_logloss: 0.652289
[20]	valid_0's multi_logloss: 0.502494	valid_1's multi_logloss: 0.522562
[30]	valid_0's multi_logloss: 0.433416	valid_1's multi_logloss: 0.460806
[40]	valid_0's multi_logloss: 0.389213	valid_1's multi_logloss: 0.423552
[50]	valid_0's multi_logloss: 0.357155	valid_1's multi_logloss: 0.397644
[60]	valid_0's multi_logloss: 0.332216	valid_1's multi_logloss: 0.379314
[70]	valid_0's multi_logloss: 0.311343	valid_1's multi_logloss: 0.364797
[80]	valid_0's multi_logloss: 0.293842	valid_1's multi_logloss: 0.35339
[90]	valid_0's multi_logloss: 0.278576	valid_1's multi_logloss: 0.343628
[100]	valid_0's multi_logloss: 0.264714	valid_1's multi_logloss: 0.335518


array([373,  50,  63,  26, 107, 106,  63,  60, 104,  44,  45,  69,  68,
        50,  57,  27,  62, 145, 117, 100,  57,  79,  23,   9,  87,  31,
        11,  10,  17,   5,  22,  21,   2, 115,  35,  67, 119, 100,  61,
        30, 103,  43,  45,  70, 109,  81, 260, 152,  20,  13,  63,  19,
        28,  12,  20,  14,  18,  27,  74,  67,  80,  54, 512,  41,  53,
        77, 150,  49,  71,  52,  90,  49,  88,  88, 783, 112, 266, 820,
       128,  87,  74,  51,  37,  40,   1,  26,   3,  26,   3,  14,  38,
        47,  80,  99,  27,  55, 107,  63, 108,  63,  51,   5,   0,  18,
        21,  21,  33,  39,  13,   2,   7,   4,   0,  12,   3,   6,  17,
         2,   3,   3,   6,   1,   3,   4,   2,   7,   2,  11,  23,   1,
         0,   0,   2,  11,   0,   6,  20,  23,   0,   0,  30,   3,   7,
         1,   0,   8,   4,   0,  26,  14,   0,  13,  23,   0,   2],
      dtype=int32)

In [ ]:

len(clf.feature_importances_)

155

In [ ]:
len(X_train_reduced.columns)

155

In [ ]:


lgbm_features = pd.DataFrame()
lgbm_features['feature'] = X_train_reduced.columns
lgbm_features['importance'] = clf.feature_importances_


lgbm_features = lgbm_features.sort_values(by=['importance'], ascending = False)

lgbm_features = lgbm_features[lgbm_features['importance']>= 50]
lgbm_features.shape


(60, 2)

In [ ]:
importances_cols = lgbm_features['feature'].to_list()

importances_cols

['Osmolality_mmol_Kg',
 'Sodium_mmol_L',
 'Blood_urea_nitrogen_mmol_L',
 'Age_Years',
 'Chloride_mmol_L',
 'Triglyceride_mmol_l',
 'LDL_Cholesterol_mmol_l',
 'Gamma_Glutamyl_Transferase_U_l',
 'Mean_Cell_Haemoglobin_pg',
 'Globulin_g_L',
 'Total_Cholesterol_mmol_l',
 'Mean_Cell_Haemoglobin_Concentration_g_dl',
 'Klotho_pg_ml',
 'Potassium_mmol_L',
 'Blood_lead_umol_l',
 'Systolic_BP_mm_hg',
 'Albumin_urine_ug_ml',
 'Waist_Circumference_cm',
 'Creatinine_unrine_umol_l',
 'Lymphocyte_number',
 '25_hydroxyvitamin_D2+D3',
 'Red_Cell_Distribution_Width_Percent',
 'Direct_HDL_Cholesterol_mmol_l',
 'Upper_Leg_Length_cm',
 'Total_Bilirubin_umol_L',
 'Uric_acid_umol_L',
 'Triglycerides_refrig_serum_mmol_L',
 'Albumin_creatinine_ratio_mg_g',
 'Urinary_Thiocyanate_ng_ml',
 'Total_Blood_Mercury_umol_l',
 'Asparate_aminotransferase_AST_U_L',
 'Body_Mass_Index_kg_m2',
 'Mean_Platelet_Volumne_fl',
 'Creatinine_umol_L',
 'RBC_folate_nmol_l',
 'Albumin_g_l',
 'Lactate_Dehydrogenase_U_l',
 'Blood_Cadmiu

In [ ]:
from sklearn.feature_selection import SelectKBest, chi2

# Create and fit selector
selector = SelectKBest(f_classif, k=51)
selector.fit(X_train_reduced, y_train)
# Get columns to keep and create new dataframe with those only
cols = selector.get_support(indices=True)
features_df_f_classif = X_train_reduced.iloc[:,cols]



In [ ]:
features_df_f_classif.head()

Age_Years  Household_size  Segmented_neutrophils_number  \
0       57.0             7.0                           5.4   
1        8.0             4.0                           3.7   
2       43.0             7.0                           3.1   
3        0.0             4.0                           3.8   
4       47.0             7.0                           3.3   

   Haematocrit_percent  Mean_Cell_Volume_fl  \
0                 52.2                 81.6   
1                 42.6                 80.6   
2                 39.3                 86.3   
3                 40.2                 87.6   
4                 42.9                 89.4   

   Red_Cell_Distribution_Width_Percent  Platelet_Count  \
0                                 14.5           328.0   
1                                 12.3           256.0   
2                                 13.8           283.0   
3                                 13.0           251.0   
4                                 13.1           324.0   

   Mean_Platelet_Volumne_fl  Klotho_pg_ml  Total_Cholesterol_mmol_l  ...  \
0                       8.1         698.0                      4.60  ...   
1                       6.6         698.0                      5.90  ...   
2                       8.9        1157.7                      4.73  ...   
3                       8.0         698.0                      4.60  ...   
4                       7.8         590.7                      5.92  ...   

   Household_income_75-100k  Household_income_greater100k  \
0                         0                             0   
1                         0                             0   
2                         0                             0   
3                         0                             0   
4                         0                             1   

   Race_Mexican_American  Race_Non_Hispanic_Black  Race_Other_Hispanic  \
0                      0                        1                    0   
1                      0                        0                    1   
2                      0                        0                    1   
3                      1                        0                    0   
4                      0                        0                    0   

   HSV1_positive  BPCuff_Child  BMI_Obese  BMI_Underweight  BMI_unknown  
0              0             0          0                0            0  
1              0             1          0                1            0  
2              1             0          1                0            0  
3              0             0          0                0            1  
4              1             0          1                0            0  

[5 rows x 51 columns]

In [ ]:
f_classif_cols = features_df_f_classif.columns
f_classif_cols

Index(['Age_Years', 'Household_size', 'Segmented_neutrophils_number',
       'Haematocrit_percent', 'Mean_Cell_Volume_fl',
       'Red_Cell_Distribution_Width_Percent', 'Platelet_Count',
       'Mean_Platelet_Volumne_fl', 'Klotho_pg_ml', 'Total_Cholesterol_mmol_l',
       'Direct_HDL_Cholesterol_mmol_l', 'Blood_Cadmium_umol_l',
       'Blood_lead_umol_l', 'Triglyceride_mmol_l', 'Urinary_Cadmium_ug_l',
       'Albumin_g_l', 'Blood_urea_nitrogen_mmol_L', 'Creatinine_umol_L',
       'Gamma_Glutamyl_Transferase_U_l', 'Triglycerides_refrig_serum_mmol_L',
       'Uric_acid_umol_L', 'Sodium_mmol_L', 'Chloride_mmol_L',
       'Osmolality_mmol_Kg', 'Globulin_g_L', 'Weight_kg', 'Height_Standing_cm',
       'Body_Mass_Index_kg_m2', 'Upper_Leg_Length_cm', 'Upper_Arm_Length_cm',
       'Arm_circumference_cm', 'Waist_Circumference_cm', 'Pulse_60s',
       'Systolic_BP_mm_hg', 'Diastolic_BP_mm_hg',
       'Average_Sagittal_Diameter_cm', 'ChildEd_10th_to_12thGrade',
       'ChildEd_5thGrade_or_lower',

In [ ]:
# Create and fit selector
selector = SelectKBest(chi2, k=51)
selector.fit(X_train_reduced, y_train)
# Get columns to keep and create new dataframe with those only
cols = selector.get_support(indices=True)
features_df_chi2 = X_train_reduced.iloc[:,cols]


In [ ]:
chi2_cols = features_df_chi2.columns
len(chi2_cols)

51

In [ ]:
from collections import Counter
from itertools import chain
feature_lists = [RFE_features, importances_cols, f_classif_cols, chi2_cols]

no_of_lists_per_name = Counter(chain.from_iterable(map(set, feature_lists)))

for name, no_of_lists in no_of_lists_per_name.most_common():
    if no_of_lists == 1:
        break # since it is ordered by count, once we get this low we are done
    print(f"'{name}' is in {no_of_lists} lists")

'Uric_acid_umol_L' is in 4 lists
'Blood_urea_nitrogen_mmol_L' is in 4 lists
'Direct_HDL_Cholesterol_mmol_l' is in 4 lists
'Body_Mass_Index_kg_m2' is in 4 lists
'Triglycerides_refrig_serum_mmol_L' is in 4 lists
'Globulin_g_L' is in 4 lists
'Blood_Cadmium_umol_l' is in 4 lists
'Age_Years' is in 4 lists
'Triglyceride_mmol_l' is in 4 lists
'Gamma_Glutamyl_Transferase_U_l' is in 4 lists
'Pulse_60s' is in 4 lists
'Klotho_pg_ml' is in 4 lists
'Creatinine_umol_L' is in 4 lists
'Systolic_BP_mm_hg' is in 4 lists
'Waist_Circumference_cm' is in 4 lists
'Total_Blood_Mercury_umol_l' is in 3 lists
'Mean_Platelet_Volumne_fl' is in 3 lists
'Urinary_Thiocyanate_ng_ml' is in 3 lists
'Red_Cell_Distribution_Width_Percent' is in 3 lists
'Osmolality_mmol_Kg' is in 3 lists
'Asparate_aminotransferase_AST_U_L' is in 3 lists
'Total_Cholesterol_mmol_l' is in 3 lists
'Albumin_g_l' is in 3 lists
'Upper_Leg_Length_cm' is in 3 lists
'Albumin_urine_ug_ml' is in 3 lists
'Sodium_mmol_L' is in 3 lists
'Cotinine_ng_ml' is

In [ ]:
from collections import Counter
from itertools import chain

feature_lists = [RFE_features, importances_cols, f_classif_cols, chi2_cols]

no_of_lists_per_name = Counter(chain.from_iterable(map(set, feature_lists)))

feature_names_to_select = []

for name, no_of_lists in no_of_lists_per_name.most_common():
    if no_of_lists == 1:
        break # since it is ordered by count, once we get this low we are done\n",
    feature_names_to_select.append(name)
    print(f"'{name}' is in {no_of_lists} lists")

'Uric_acid_umol_L' is in 4 lists
'Blood_urea_nitrogen_mmol_L' is in 4 lists
'Direct_HDL_Cholesterol_mmol_l' is in 4 lists
'Body_Mass_Index_kg_m2' is in 4 lists
'Triglycerides_refrig_serum_mmol_L' is in 4 lists
'Globulin_g_L' is in 4 lists
'Blood_Cadmium_umol_l' is in 4 lists
'Age_Years' is in 4 lists
'Triglyceride_mmol_l' is in 4 lists
'Gamma_Glutamyl_Transferase_U_l' is in 4 lists
'Pulse_60s' is in 4 lists
'Klotho_pg_ml' is in 4 lists
'Creatinine_umol_L' is in 4 lists
'Systolic_BP_mm_hg' is in 4 lists
'Waist_Circumference_cm' is in 4 lists
'Total_Blood_Mercury_umol_l' is in 3 lists
'Mean_Platelet_Volumne_fl' is in 3 lists
'Urinary_Thiocyanate_ng_ml' is in 3 lists
'Red_Cell_Distribution_Width_Percent' is in 3 lists
'Osmolality_mmol_Kg' is in 3 lists
'Asparate_aminotransferase_AST_U_L' is in 3 lists
'Total_Cholesterol_mmol_l' is in 3 lists
'Albumin_g_l' is in 3 lists
'Upper_Leg_Length_cm' is in 3 lists
'Albumin_urine_ug_ml' is in 3 lists
'Sodium_mmol_L' is in 3 lists
'Cotinine_ng_ml' is

In [ ]:
len(feature_names_to_select)

68

In [ ]:
X_train_multiselected = X_train[feature_names_to_select]

In [ ]:
X_test_multiselected = X_test[feature_names_to_select]

In [ ]:
X_train_multiselected.head()

Uric_acid_umol_L  Blood_urea_nitrogen_mmol_L  \
0             315.2                        4.28   
1             315.2                        4.28   
2             315.2                        4.28   
3             315.2                        4.28   
4             428.3                        3.57   

   Direct_HDL_Cholesterol_mmol_l  Body_Mass_Index_kg_m2  \
0                           51.0                   19.7   
1                           89.0                   16.3   
2                           39.0                   30.1   
3                           51.0                   25.0   
4                           47.0                   31.1   

   Triglycerides_refrig_serum_mmol_L  Globulin_g_L  Blood_Cadmium_umol_l  \
0                              1.264          28.0                  5.87   
1                              1.264          28.0                  0.00   
2                              1.660          30.0                  1.96   
3                              1.264          28.0                  1.96   
4                              1.569          23.0                  4.89   

   Age_Years  Triglyceride_mmol_l  Gamma_Glutamyl_Transferase_U_l  ...  \
0       57.0                1.073                            18.0  ...   
1        8.0                1.073                            18.0  ...   
2       43.0                1.569                            25.0  ...   
3        0.0                1.073                            18.0  ...   
4       47.0                1.558                            20.0  ...   

   Upper_Arm_Length_cm  Race_Mexican_American  HSV1_positive  \
0                 35.0                      0              0   
1                 26.9                      0              0   
2                 35.0                      0              1   
3                 35.5                      1              0   
4                 39.8                      0              1   

   ChildEd_5thGrade_or_lower  BPCuff_Child  Weight_kg  BMI_unknown  \
0                          0             0       50.5            0   
1                          1             1       29.4            0   
2                          0             0       71.0            0   
3                          0             0        5.1            1   
4                          0             0      105.3            0   

   Household_income_75-100k  ChildEd_None_KG  ChildEd_6th_to_9thGrade  
0                         0                0                        0  
1                         0                0                        0  
2                         0                0                        0  
3                         0                0                        0  
4                         0                0                        0  

[5 rows x 68 columns]

In [ ]:
X_train_multiselected.to_csv('Data/multiselected_data/X_train_multiselected.csv')

In [ ]:
X_test_multiselected.to_csv('Data/multiselected_data/X_test_multiselected.csv')